# Machine Fault Classification with MAFAULDA

This notebook explores data from [MAFAULDA](https://www02.smt.ufrj.br/~offshore/mfs/page_01.html) which is a multivariate time-series dataset acquired by sensors on Machinery Fault Simulator (MFS) Alignment-Balance-Vibration (ABVT). Data from [Kaggle](https://www.kaggle.com/datasets/uysalserkan/fault-induction-motor-dataset/data) includes two different simulated states: normal function and imbalance fault. 

The objective is to build a time-series classification model to distinguish between normal and imbalance motor condition.

#### Data are stored in CSV files and saved in a label-based folder structure

In [1]:
!tree ../data/. -L 3 -I "*.csv"

../data/.
├── imbalance
│   └── imbalance
│       ├── 10g
│       ├── 15g
│       ├── 20g
│       ├── 25g
│       ├── 30g
│       ├── 35g
│       └── 6g
└── normal
    └── normal

12 directories, 0 files


#### From the folder structure we can extract the labels

In [2]:
import os

labels = []
for dirname, _, filenames in os.walk("../data"):
    for filename in filenames:
        file_addr = os.path.join(dirname, filename)
        class_name = "-".join(file_addr.split('.csv')[0].split("/")[-3:-1])
        labels.append(class_name)

print(set(labels))

{'imbalance-30g', 'imbalance-15g', 'imbalance-25g', 'imbalance-20g', 'imbalance-35g', 'imbalance-6g', 'normal-normal', 'imbalance-10g'}


## Data Frame

According with their website:
- There are 8 features: 'tachometer', 'underhang_axial', 'underhang_radiale', 'underhang_tangential', 'overhang_axial', 'overhang_radiale', 'overhang_tangential', 'microphone'.
- Each sequence was generated at 50 kHz sampling rate during 5 s, totaling 250.000 samples.

Let's instanciate and concatenate all dataframes that belongs to normal functioning label.

In [7]:
import os
import pandas as pd
from random import sample

col_names = [
    'tachometer', 'underhang_axial', 'underhang_radiale', 'underhang_tangential',
    'overhang_axial', 'overhang_radiale', 'overhang_tangential', 'microphone'
]

normal_dfs = []
for dirname, _, filenames in os.walk("../data"):
    for filename in filenames:
        file_addr = os.path.join(dirname, filename)
        if file_addr.endswith('.csv'):
            # Infer labels from folder structure
            label = "-".join(file_addr.split('.csv')[0].split("/")[-3:-1])

            if "normal" in label:
                print(file_addr)
                df = pd.read_csv(file_path, names=col_names)
                normal_dfs.append(df)

print([f"{df.shape}" for df in normal_dfs])

../data/normal/normal/12.288.csv
../data/normal/normal/13.1072.csv
../data/normal/normal/14.336.csv
../data/normal/normal/15.1552.csv
../data/normal/normal/16.1792.csv
../data/normal/normal/17.2032.csv
../data/normal/normal/18.432.csv
../data/normal/normal/19.6608.csv
../data/normal/normal/20.2752.csv
../data/normal/normal/21.7088.csv
../data/normal/normal/22.3232.csv
../data/normal/normal/23.552.csv
../data/normal/normal/24.576.csv
../data/normal/normal/25.6.csv
../data/normal/normal/26.624.csv
../data/normal/normal/27.4432.csv
../data/normal/normal/28.8768.csv
../data/normal/normal/29.4912.csv
../data/normal/normal/30.72.csv
../data/normal/normal/31.744.csv
../data/normal/normal/32.9728.csv
../data/normal/normal/33.5872.csv
../data/normal/normal/34.2016.csv
../data/normal/normal/35.4304.csv
../data/normal/normal/36.4544.csv
../data/normal/normal/37.6832.csv
../data/normal/normal/38.2976.csv
../data/normal/normal/39.3216.csv
../data/normal/normal/40.3456.csv
../data/normal/normal/41.7

In [8]:
normal_df = pd.concat(normal_dfs, ignore_index=True)

normal_df.describe()

tachometer  underhang_axial  underhang_radiale  underhang_tangential  \
count  1.225000e+07     1.225000e+07       1.225000e+07          1.225000e+07   
mean   1.024785e-03     2.953720e-02       7.297756e-04          8.317160e-04   
std    1.597937e+00     1.238304e+00       3.365933e-01          4.673923e-02   
min   -1.159100e+00    -4.589800e+00      -2.003700e+00         -2.186500e-01   
25%   -6.052700e-01    -9.648400e-01      -2.714825e-01         -3.177200e-02   
50%   -5.507550e-01     1.678850e-01       3.253400e-02          3.303400e-03   
75%   -4.748875e-01     1.177825e+00       3.121600e-01          3.450600e-02   
max    5.093000e+00     2.009700e+00       6.776800e-01          2.270500e-01   

       overhang_axial  overhang_radiale  overhang_tangential    microphone  
count    1.225000e+07      1.225000e+07         1.225000e+07  1.225000e+07  
mean     9.245404e-03      5.104041e-03         3.855342e-02  1.462299e-02  
std      1.393458e-01      3.592690e-02         6.781154e-01  1.227685e-01  
min     -6.115700e-01     -1.459500e-01        -2.037600e+00 -2.686400e-01  
25%     -8.811175e-02     -1.904200e-02        -4.425250e-01 -8.873400e-02  
50%      2.394700e-02      6.570500e-03         5.070450e-02 -4.500900e-03  
75%      1.165300e-01      3.114300e-02         4.879000e-01  1.011300e-01  
max      3.431600e-01      1.046600e-01         2.350300e+00  6.089600e-01

In [4]:
from ydata_profiling import ProfileReport

profile = ProfileReport(normal_df, title="Normal Data")
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [5]:
profile.to_file("normal_data_report.html")

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [9]:
len(normal_dfs)

49